## Surprise 모듈 활용 모델

In [2]:
from utils.Dataloader import load_ratings, load_movies
from sklearn.decomposition import randomized_svd, non_negative_factorization
from sklearn.metrics.pairwise import cosine_similarity
from sklearn.metrics import ndcg_score
from surprise import Dataset, Reader
import numpy as np
from surprise import Dataset
from surprise.model_selection import GridSearchCV
from collections import defaultdict


In [ ]:
# Surprise 모듈 사용시
data = Dataset.load_builtin('ml-100k', prompt=False) #예시 코드에서 사용한 데이터
print(data)

### 데이터 호출

#### rating 데이터 호출 및 전처리

In [3]:
# 데이터 폴더 경로
DATA_PATH = "./datasets/"
# ratings 데이터 로드
ratings_df = load_ratings(DATA_PATH)
# 데이터프레임 변환 -> 튜플 리스트
t_ratings_df = [tuple(x) for x in ratings_df.values]

t_ratings_df[:10]

[(1, 1193, 5, 978300760),
 (1, 661, 3, 978302109),
 (1, 914, 3, 978301968),
 (1, 3408, 4, 978300275),
 (1, 2355, 5, 978824291),
 (1, 1197, 3, 978302268),
 (1, 1287, 5, 978302039),
 (1, 2804, 5, 978300719),
 (1, 594, 4, 978302268),
 (1, 919, 4, 978301368)]

In [4]:
#코사인 유사도 함수
def compute_cos_similarity(v1, v2):
  norm1 = np.sqrt(np.sum(np.square(v1)))
  norm2 = np.sqrt(np.sum(np.square(v2)))
  dot = np.dot(v1, v2)
  return dot / (norm1 * norm2)

#### movie_id & title 매치 함수

In [5]:
def get_movie_info_by_id(movie_id, movies_df):
    movie_info = movies_df[movies_df['movieId'] == movie_id]
    return movie_info

def title(result):
    DATA_PATH = "./datasets/"
    movies_df = load_movies(DATA_PATH)
    m_titles = []

    for i in result:
        movie_info = get_movie_info_by_id(i, movies_df)
        movie_titles = movies_df[movies_df['movieId'] == i]['title'].tolist()  # 영화 ID에 해당하는 모든 제목을 가져옴
        m_titles.append(movie_titles) # 리스트 확장을 사용하여 여러 개의 제목을 추가

    return m_titles

#### 평가지표 순위 고려
real item에 대한 순위를 고려하기 위함
1. 평점 (평점이 높은 영화)
2. 시간 (가장 최근에 본 리뷰를 남긴 영화)
ndcg나 hit rate에 적용할 수 있는 총 결과 생성

In [6]:
#평점 순으로 정렬
from collections import defaultdict

def create_user_movie_list(data):
    user_movie_list = defaultdict(list)
    
    for user_id, movie_id, rating, timestamp in data:
        user_movie_list[user_id].append((movie_id, rating))
    
    for user_id in user_movie_list:
        user_movie_list[user_id].sort(key=lambda x: x[1], reverse=True)  # 평점으로 정렬
    
    return user_movie_list

user_movie_list = create_user_movie_list(t_ratings_df)
user_movie_list


defaultdict(list,
            {1: [(1193, 5),
              (2355, 5),
              (1287, 5),
              (2804, 5),
              (595, 5),
              (1035, 5),
              (3105, 5),
              (1270, 5),
              (527, 5),
              (48, 5),
              (1836, 5),
              (1022, 5),
              (150, 5),
              (1, 5),
              (1961, 5),
              (1028, 5),
              (1029, 5),
              (2028, 5),
              (3408, 4),
              (594, 4),
              (919, 4),
              (938, 4),
              (2398, 4),
              (2918, 4),
              (2791, 4),
              (2018, 4),
              (2797, 4),
              (1097, 4),
              (1721, 4),
              (1545, 4),
              (2294, 4),
              (3186, 4),
              (1566, 4),
              (588, 4),
              (1907, 4),
              (783, 4),
              (2762, 4),
              (1962, 4),
              (2692, 4),
              (26

In [7]:
len(user_movie_list)

6040

#### 평가지표 함수
Precision&Recall
-> 실제 시청 리스트 적용

In [8]:
def evaluate_precision_recall(all_user_recommendations, user_movie_list, k=10):
    # --- input : 모든 유저에 대한 추천 영화 목록, 모든 유저들의 시청 영화 목록, 평가할 영화 개수
    # 점수 초기화
    total_precision_at_k = 0.0
    total_recall_at_k = 0.0
    num_users = len(all_user_recommendations)

    for user_id, recommended_items in all_user_recommendations.items():
        # 실제 유저가 시청한 목록에서 영화 정보 순회
        actual_items = [item[0] for item in user_movie_list[user_id]]
        precision_at_k, recall_at_k = calculate_precision_recall(actual_items, recommended_items, k=10)
        total_precision_at_k += precision_at_k
        total_recall_at_k += recall_at_k

    avg_precision_at_k = total_precision_at_k / num_users
    avg_recall_at_k = total_recall_at_k / num_users

    return avg_precision_at_k, avg_recall_at_k

def calculate_precision_recall(actual_items, recommended_items, k):
    # 추천 리스트와 실제 시청 목록을 비교하여 중복된 아이템 개수
    num_recommended_at_k = len(set(recommended_items[:k]).intersection(actual_items))
    precision_at_k = num_recommended_at_k / k if k > 0 else 0.0
    recall_at_k = num_recommended_at_k / len(actual_items) if len(actual_items) > 0 else 0.0
    return precision_at_k, recall_at_k


NDCG@k & Hit@k 함수

In [9]:
def evaluate_recommendation_metrics(user_movie_list, all_user_recommendations, k=10):
    user_movie_dict = defaultdict(list)
    
    for user, movie_list in user_movie_list.items():
        user_movie_dict[user] = [movie[0] for movie in movie_list]
    
    def calculate_dcg(user, recommendations):
        dcg = 0
        for i, movie in enumerate(recommendations, 1):
            if movie in user_movie_dict[user]:
                relevance = 1
            else:
                relevance = 0
            dcg += (2 ** relevance - 1) / np.log2(i + 1)
        return dcg
    
    def calculate_idcg(user, recommendations):
        idcg = 0
        sorted_movies = sorted(user_movie_dict[user], key=lambda movie: recommendations.index(movie) if movie in recommendations else float('inf'))
        for i, movie in enumerate(sorted_movies, 1):
            idcg += (2 ** 1 - 1) / np.log2(i + 1)
        return idcg
    
    def calculate_ndcg(user, recommendations):
        dcg = calculate_dcg(user, recommendations)
        idcg = calculate_idcg(user, recommendations)
        if idcg == 0:
            return 0
        ndcg = dcg / idcg
        return ndcg if ndcg != 0 else 0  # 0으로 나누는 문제 처리

    
    def calculate_hit_at_k(user, recommendations, k=10):
        relevant_watched = [movie for movie in recommendations if movie in user_movie_dict[user]]
        hit_at_k = 1 if len(relevant_watched) >= k else 0

        # relevant_watched 리스트의 길이가 0인 경우 0으로 나누는 것을 방지하기 위한 조치
        if len(relevant_watched) == 0:
            hit_at_k = 0
        return hit_at_k
    
    # 모든 점수를 딕셔너리 형태로 저장
    ndcg_scores = {}
    hit_at_k_scores = {}
    
    for user, recommendations in all_user_recommendations.items():
        ndcg_scores[user] = calculate_ndcg(user, recommendations)
        hit_at_k_scores[user] = calculate_hit_at_k(user, recommendations, k)
    
    def calculate_average_score(scores_dict):
        total_score = sum(scores_dict.values())
        average_score = total_score / len(scores_dict)
        return average_score
    
    average_ndcg = calculate_average_score(ndcg_scores)
    average_hit_at_k = calculate_average_score(hit_at_k_scores)
    
    return average_ndcg, average_hit_at_k


In [150]:
def evaluate_recommendation_metrics2(user_movie_list, all_user_recommendations, k=10):
    user_movie_dict = defaultdict(list)
    
    for user, movie_list in user_movie_list.items():
        user_movie_dict[user] = [movie[0] for movie in movie_list]
    
    def calculate_dcg(user, recommendations):
        dcg = 0
        for i, movie in enumerate(recommendations, 1):
            if movie in user_movie_dict[user]:
                relevance = 1
            else:
                relevance = 0
            dcg += (2 ** relevance - 1) / np.log2(i + 1)
        return dcg
    
    def calculate_idcg(user, recommendations):
        idcg = 0
        sorted_movies = sorted(user_movie_dict[user], key=lambda movie: recommendations.tolist().index(movie) if movie in recommendations else float('inf'))
        for i, movie in enumerate(sorted_movies, 1):
            idcg += (2 ** 1 - 1) / np.log2(i + 1)
        return idcg
    
    def calculate_ndcg(user, recommendations):
        dcg = calculate_dcg(user, recommendations)
        idcg = calculate_idcg(user, recommendations)
        if idcg == 0:
            return 0
        ndcg = dcg / idcg
        return ndcg if ndcg != 0 else 0  # 0으로 나누는 문제 처리

    
    def calculate_hit_at_k(user, recommendations, k=10):
        relevant_watched = [movie for movie in recommendations if movie in user_movie_dict[user]]
        hit_at_k = 1 if len(relevant_watched) >= k else 0
        return hit_at_k
    
    # 모든 점수를 딕셔너리 형태로 저장
    ndcg_scores = {}
    hit_at_k_scores = {}
    
    for user, recommendations in all_user_recommendations.items():
        ndcg_scores[user] = calculate_ndcg(user, recommendations)
        hit_at_k_scores[user] = calculate_hit_at_k(user, recommendations, k)
    
    def calculate_average_score(scores_dict):
        total_score = sum(scores_dict.values())
        average_score = total_score / len(scores_dict)
        return average_score
    
    average_ndcg = calculate_average_score(ndcg_scores)
    average_hit_at_k = calculate_average_score(hit_at_k_scores)
    
    return average_ndcg, average_hit_at_k


네 가지 모델을 비교한 결과,
SVD++가 RMSE, MAE 오차가 가장 적어 성능이 우수하나 모델 학습 및 검증 시간이 가장 오래 걸림.<br>
따라서 시간 소요가 적절하면서 성능도 좋은 SVD 모델을 사용하는 것을 고려

### 하이브리드 모델

#### A. SVD(행렬 분해) + 사용자 기반 추천 모델

In [10]:
#데이터프레임을 NumPy 배열로 변환
raw_data = np.array(t_ratings_df, dtype=int) #튜플링 된 rating_df
raw_data[:, 0] -= 1 # userID를 0부터 시작하도록 조정
raw_data[:, 1] -= 1 # movieID를 0부터 시작하도록 조정

n_users = np.max(raw_data[:, 0]) #사용자 최대 갯수
n_movies = np.max(raw_data[:, 1]) #영화 최대 갯수
shape = (n_users + 1, n_movies + 1) # 행렬 크기 결정
print(shape)

adj_matrix = np.ndarray(shape, dtype=int) # 위의 행렬 크기에 맞는 빈 행렬 생성
print(adj_matrix)
# 행렬 내용 채우기
for user_id, movie_id, rating, time in raw_data:
  adj_matrix[user_id][movie_id] = rating

#행렬분해 -randomized_svd 활용, 주성분 수 2개
# U : 사용자, V : 아이템, S : 특이값 벡터
U, S, V = randomized_svd(adj_matrix, n_components=2)
S = np.diag(S) # 특잇값 행렬 S를 대각 행렬 형태로 변환
print(U.shape)
print(S.shape) # 잠재요인을 찾는 행렬
print(V.shape)
np.matmul(np.matmul(U, S), V) # 변환된 행렬 U, S, V를 다시 곱하여 원래 행렬을 근사적으로 재구성 - 점수 복원

(6040, 3952)
[[0 0 0 ... 0 0 0]
 [0 0 0 ... 0 0 0]
 [0 0 0 ... 0 0 0]
 ...
 [0 0 0 ... 0 0 0]
 [0 0 0 ... 0 0 0]
 [0 0 0 ... 0 0 0]]
(6040, 2)
(2, 2)
(2, 3952)


array([[ 0.60332513,  0.17737913,  0.10450221, ...,  0.02542992,
         0.01292006,  0.12395444],
       [ 1.27130113,  0.46798157,  0.27232846, ...,  0.04259506,
         0.01640812,  0.22402371],
       [ 0.71226823,  0.29018226,  0.16806108, ...,  0.02060001,
         0.00597981,  0.11447211],
       ...,
       [ 0.15892504,  0.0256363 ,  0.01586029, ...,  0.00915844,
         0.00582436,  0.04097067],
       [ 0.66674863, -0.06294511, -0.0277904 , ...,  0.05831083,
         0.04400951,  0.23914817],
       [ 1.94412574,  0.0290688 ,  0.03659432, ...,  0.14522507,
         0.10391593,  0.613443  ]])

#### B. 사용자 기반 추천

#### 1) 사용자 기반 추천 - 행렬 비사용 시

예시 결과 출력

In [12]:
# 사용자 지정 및 코사인 유사도 계산
my_id = 0  # 원하는 사용자의 ID 입력
my_vector = adj_matrix[my_id]
top_n = 10  # 원하는 상위 영화 개수
best_match, best_match_id, best_match_vector = -1, -1, []

for user_id, user_vector in enumerate(adj_matrix):
  if my_id != user_id:
    cos_similarity = compute_cos_similarity(my_vector, user_vector)
    if cos_similarity > best_match:
      best_match = cos_similarity
      best_match_id = user_id
      best_match_vector = user_vector

print('Best Match: {}, Best Match Id:{}'.format(best_match, best_match_id))

recommend_list = []
for i, (log1, log2) in enumerate(zip(my_vector, best_match_vector)):
    if log1 < 1. and log2 > 0.: #사용자가 평점을 안준 영화 & 다른 사용자가 평점을 준 영화
        recommend_list.append(i)
        
# 상위 N개의 추천 영화만 선택
top_recommendations = recommend_list[:top_n]
print(f'사용자 {my_id+1}에게 코사인 유사도를 사용한 상위 {top_n}개 영화 리스트: {top_recommendations}')
print(f'{my_id+1} 사용자와 가장 유사한 사용자 ID: {best_match_id+1}')
modified_recommendations = [movie + 1 for movie in top_recommendations]
print(f'수정된 추천 영화 리스트: {modified_recommendations}')

title(modified_recommendations)

Best Match: 0.41211706435523543, Best Match Id:5342
사용자 1에게 코사인 유사도를 사용한 상위 10개 영화 리스트: [456, 592, 909, 1022, 1220, 1229, 1342, 1616, 2077, 2079]
1 사용자와 가장 유사한 사용자 ID: 5343
수정된 추천 영화 리스트: [457, 593, 910, 1023, 1221, 1230, 1343, 1617, 2078, 2080]


[['Fugitive, The (1993)'],
 ['Silence of the Lambs, The (1991)'],
 ['Some Like It Hot (1959)'],
 ['Winnie the Pooh and the Blustery Day (1968)'],
 ['Godfather: Part II, The (1974)'],
 ['Annie Hall (1977)'],
 ['Cape Fear (1991)'],
 ['L.A. Confidential (1997)'],
 ['Jungle Book, The (1967)'],
 ['Lady and the Tramp (1955)']]

모든 결과 저장

In [16]:
# 딕셔너리 형태로 모든 사용자의 추천 영화 리스트 저장
recommendations_dict = {}
for user_id, user_vector in enumerate(adj_matrix):
    if my_id != user_id:
        recommend_list = []
        for i, (log1, log2) in enumerate(zip(my_vector, user_vector)):
            if log2 > 0.:
                recommend_list.append(i)
        recommendations_dict[user_id] = recommend_list[:top_n]

print(recommendations_dict)

{1: [20, 94, 109, 162, 164, 234, 264, 291, 317, 348], 2: [103, 259, 479, 551, 589, 592, 647, 652, 732, 1048], 3: [259, 479, 1035, 1096, 1195, 1197, 1200, 1209, 1213, 1239], 4: [5, 15, 23, 28, 31, 33, 35, 38, 40, 46], 5: [0, 16, 33, 47, 198, 265, 295, 363, 367, 376], 6: [5, 109, 348, 376, 379, 441, 456, 473, 479, 588], 7: [0, 3, 13, 15, 16, 23, 24, 35, 38, 41], 8: [0, 15, 24, 46, 49, 149, 161, 222, 299, 317], 9: [0, 1, 6, 23, 31, 47, 61, 103, 109, 115], 10: [35, 46, 49, 84, 87, 103, 109, 215, 230, 245], 11: [110, 592, 812, 857, 918, 922, 933, 998, 1192, 1197], 12: [1, 9, 20, 49, 59, 109, 152, 164, 259, 295], 13: [295, 607, 1224, 1262, 1967, 1981, 2242, 2395, 2571, 2685], 14: [5, 31, 46, 49, 69, 72, 103, 109, 140, 159], 15: [265, 1268, 1681, 1910, 2354, 2368, 2391, 2393, 2484, 2554], 16: [23, 29, 31, 33, 49, 75, 109, 161, 162, 163], 17: [0, 1, 9, 16, 25, 28, 33, 43, 46, 47], 18: [0, 9, 16, 31, 33, 46, 75, 109, 110, 164], 19: [46, 69, 109, 456, 588, 647, 1239, 1370, 1374, 1467], 20: [0, 5

평가지표 적용

Ndcg@10, Hit@10

In [18]:
evaluate_recommendation_metrics(user_movie_list, recommendations_dict, k=10)

(0.008350057915653138, 0.0)

Precision & Recall

In [17]:
evaluate_precision_recall(recommendations_dict, user_movie_list, 10)

(0.061003477396920636, 0.0038849885143950815)

#### 2) 사용자 기반 추천 - 행렬 사용 시

예시 결과 출력

In [19]:
# 사용자 지정 및 코사인 유사도 계산
my_id = 0  # 원하는 사용자의 ID 입력
my_vector = U[my_id]
top_n = 10  # 원하는 상위 영화 개수
best_match, best_match_id, best_match_vector = -1, -1, []

for user_id, user_vector in enumerate(U):
  if my_id != user_id:
    cos_similarity = compute_cos_similarity(my_vector, user_vector)
    if cos_similarity > best_match:
      best_match = cos_similarity
      best_match_id = user_id
      best_match_vector = user_vector

print('Best Match: {}, Best Match Id:{}'.format(best_match, best_match_id))

recommend_list = []
for i, (log1, log2) in enumerate(zip(adj_matrix[my_id], adj_matrix[best_match_id])):
  if log2 > 0.:
    recommend_list.append(i)
        
# 상위 N개의 추천 영화만 선택
top_recommendations = recommend_list[:top_n]
print(f'사용자 {my_id+1}에게 코사인 유사도를 사용한 상위 {top_n}개 영화 리스트: {top_recommendations}')
print(f'{my_id+1} 사용자와 가장 유사한 사용자 ID: {best_match_id+1}')
modified_recommendations = [movie + 1 for movie in top_recommendations]
print(f'수정된 추천 영화 리스트: {modified_recommendations}')

title(modified_recommendations)

Best Match: 0.9999999999868072, Best Match Id:3877
사용자 1에게 코사인 유사도를 사용한 상위 10개 영화 리스트: [6, 9, 10, 15, 20, 23, 24, 38, 44, 49]
1 사용자와 가장 유사한 사용자 ID: 3878
수정된 추천 영화 리스트: [7, 10, 11, 16, 21, 24, 25, 39, 45, 50]


[['Sabrina (1995)'],
 ['GoldenEye (1995)'],
 ['American President, The (1995)'],
 ['Casino (1995)'],
 ['Get Shorty (1995)'],
 ['Powder (1995)'],
 ['Leaving Las Vegas (1995)'],
 ['Clueless (1995)'],
 ['To Die For (1995)'],
 ['Usual Suspects, The (1995)']]

모든 결과 저장

 특정 사용자와 유사한 사용자를 찾는 대신, 모든 사용자에 대해 유사한 사용자를 선정하고<br>
 그들의 영화 시청 기록을 바탕으로 추천하는 방식<br>
 즉, 모든 사용자를 대상으로 유사한 사용자를 선정하고, 그들의 영화 시청 기록을 통합하여 최종적인 추천 영화를 생성<br>
 이 방식은 모든 사용자의 시청 기록을 활용하여 추천을 생성하므로 더 포괄적인 결과를 나타냄<br>

In [20]:
def get_user_top_n_recommendations_limit(adj_matrix, my_id, U, limit=5, top_n=10):
    # 자기 자신을 제외한 모든 사용자와의 유사도 계산
    similarities = cosine_similarity([U[my_id]], U).flatten()
    similar_user_ids = np.argsort(similarities)[-limit-1:-1]  # 유사도가 가장 높은 사용자 ID 선별 (자기 자신 제외)
    
    recommendations = []
    for user_id in similar_user_ids:
        recommend_list = []
        for i, log in enumerate(adj_matrix[user_id]):
            if log > 0:  # 유사한 사용자가 시청한 영화
                recommend_list.append(i + 1)  # 1을 더해 영화 ID를 1부터 시작하도록 조정
        recommendations.extend(recommend_list)
    
    unique_recommendations = list(set(recommendations))
    return unique_recommendations[:top_n]

all_user_top_n_recommendations = {}

for user_id in range(n_users):
    user_top_n_recommendations = get_user_top_n_recommendations_limit(adj_matrix, user_id, U, limit=5, top_n=10)
    all_user_top_n_recommendations[user_id + 1] = user_top_n_recommendations

print(all_user_top_n_recommendations)


{1: [1, 2051, 2054, 7, 10, 11, 2060, 15, 16, 17], 2: [1, 2, 2052, 16, 17, 2071, 25, 34, 39, 2092], 3: [1, 2, 3, 5, 6, 2054, 11, 2059, 2060, 16], 4: [1, 2, 2051, 4, 2053, 2054, 7, 2057, 2058, 2059], 5: [1, 2, 3, 3257, 2052, 6, 2054, 7, 10, 11], 6: [2048, 1, 2, 6, 7, 2054, 10, 11, 2058, 2060], 7: [1, 2, 2053, 6, 10, 11, 2058, 15, 16, 19], 8: [2048, 1, 2050, 3, 5, 6, 2054, 11, 2060, 2064], 9: [1, 2, 2052, 2054, 17, 2067, 2069, 2071, 24, 32], 10: [1, 3, 2054, 6, 2058, 11, 16, 17, 2064, 19], 11: [1, 2, 3, 2053, 2054, 6, 10, 11, 2058, 14], 12: [1537, 3, 515, 523, 527, 3089, 531, 2067, 2069, 2070], 13: [1, 2, 3, 4, 2052, 6, 7, 8, 9, 2058], 14: [1, 7, 11, 2060, 15, 16, 19, 2067, 21, 2072], 15: [1, 2, 1025, 2053, 6, 2054, 1544, 3078, 10, 2571], 16: [1, 2, 3, 2050, 5, 6, 7, 2052, 2053, 10], 17: [1, 4, 5, 2054, 7, 2057, 10, 11, 12, 2059], 18: [1, 2052, 2053, 6, 2054, 2058, 11, 2059, 2060, 16], 19: [1, 3, 2054, 7, 11, 2060, 15, 16, 17, 19], 20: [1, 2, 3, 2052, 2054, 10, 11, 2059, 2060, 2058], 21: 

평가지표 적용

Precision & Recall

In [21]:
evaluate_precision_recall(all_user_top_n_recommendations, user_movie_list, 10)

(0.1582050008279559, 0.010481012634422048)

Ndcg & Hit

In [22]:
evaluate_recommendation_metrics(user_movie_list, all_user_top_n_recommendations, 10)

(0.025773781795959527, 0.0011591323066732903)

#### 3) 비음수 행렬 분해

In [25]:
adj_matrix #사용자 평점 매트릭스

array([[5, 0, 0, ..., 0, 0, 0],
       [0, 0, 0, ..., 0, 0, 0],
       [0, 0, 0, ..., 0, 0, 0],
       ...,
       [0, 0, 0, ..., 0, 0, 0],
       [0, 0, 0, ..., 0, 0, 0],
       [3, 0, 0, ..., 0, 0, 0]])

In [26]:
A, B, iter = non_negative_factorization(adj_matrix, n_components=2)

In [27]:
print(A.shape)
print(B.shape)
print(iter)

(6040, 2)
(2, 3952)
63


In [28]:
np.matmul(A,B)

array([[0.59369832, 0.1773086 , 0.1035335 , ..., 0.02491037, 0.0126654 ,
        0.12166625],
       [1.26610997, 0.46145633, 0.26902974, ..., 0.04260549, 0.01715927,
        0.2235496 ],
       [0.71449515, 0.29348069, 0.17096232, ..., 0.01986921, 0.0057741 ,
        0.11190183],
       ...,
       [0.15263133, 0.0226815 , 0.01336021, ..., 0.00929474, 0.00596337,
        0.0411488 ],
       [0.76659261, 0.01059084, 0.00729107, ..., 0.0597247 , 0.04216557,
        0.25120164],
       [1.92514278, 0.02659675, 0.01831004, ..., 0.14998654, 0.10589032,
        0.63084228]])

사용자 기반 추천

In [29]:
# 사용자 지정 및 코사인 유사도 계산
my_id = 0  # 원하는 사용자의 ID 입력
my_vector = A[my_id]
top_n = 10  # 원하는 상위 영화 개수
best_match, best_match_id, best_match_vector = -1, -1, []

for user_id, user_vector in enumerate(A):
  if my_id != user_id:
    cos_similarity = compute_cos_similarity(my_vector, user_vector)
    if cos_similarity > best_match:
      best_match = cos_similarity
      best_match_id = user_id
      best_match_vector = user_vector

print('Best Match: {}, Best Match Id:{}'.format(best_match, best_match_id))

recommend_list = []
for i, (log1, log2) in enumerate(zip(adj_matrix[my_id], adj_matrix[best_match_id])):
  if log1 < 1 and log2 > 0.:
    recommend_list.append(i)
        
# 상위 N개의 추천 영화만 선택
top_recommendations = recommend_list[:top_n]
print(f'사용자 {my_id+1}에게 코사인 유사도를 사용한 상위 {top_n}개 영화 리스트: {top_recommendations}')
print(f'{my_id+1} 사용자와 가장 유사한 사용자 ID: {best_match_id+1}')
modified_recommendations = [movie + 1 for movie in top_recommendations]
print(f'수정된 추천 영화 리스트: {modified_recommendations}')

title(modified_recommendations)

Best Match: 0.9999999978358205, Best Match Id:122
사용자 1에게 코사인 유사도를 사용한 상위 10개 영화 리스트: [5, 10, 13, 15, 19, 20, 21, 24, 35, 44]
1 사용자와 가장 유사한 사용자 ID: 123
수정된 추천 영화 리스트: [6, 11, 14, 16, 20, 21, 22, 25, 36, 45]


[['Heat (1995)'],
 ['American President, The (1995)'],
 ['Nixon (1995)'],
 ['Casino (1995)'],
 ['Money Train (1995)'],
 ['Get Shorty (1995)'],
 ['Copycat (1995)'],
 ['Leaving Las Vegas (1995)'],
 ['Dead Man Walking (1995)'],
 ['To Die For (1995)']]

모든 결과 저장

In [30]:
def get_user_top_n_recommendations_limit(adj_matrix, my_id, A, limit=5, top_n=10):
    # 자기 자신을 제외한 모든 사용자와의 유사도 계산
    similarities = cosine_similarity([A[my_id]], A).flatten()
    similar_user_ids = np.argsort(similarities)[-limit-1:-1]  # 유사도가 가장 높은 사용자 ID 선별 (자기 자신 제외)
    
    recommendations = []
    for user_id in similar_user_ids:
        recommend_list = []
        for i, log in enumerate(adj_matrix[user_id]):
            if log > 0:  # 유사한 사용자가 시청한 영화
                recommend_list.append(i + 1)  # 1을 더해 영화 ID를 1부터 시작하도록 조정
        recommendations.extend(recommend_list)
    
    unique_recommendations = list(set(recommendations))
    return unique_recommendations[:top_n]

all_user_top_n_recommendations = {}

for user_id in range(n_users):
    user_top_n_recommendations = get_user_top_n_recommendations_limit(adj_matrix, user_id, A, limit=5, top_n=10)
    all_user_top_n_recommendations[user_id + 1] = user_top_n_recommendations

print(all_user_top_n_recommendations)


{1: [1, 2, 4, 6, 2054, 2058, 11, 14, 16, 17], 2: [1, 2, 3, 2052, 2053, 2054, 6, 5, 7, 10], 3: [1, 2, 2049, 6, 7, 2054, 10, 2058, 11, 17], 4: [1, 2050, 2, 3, 5, 2054, 6, 8, 2058, 11], 5: [1, 2054, 6, 10, 2058, 2064, 16, 18, 2069, 21], 6: [1, 2, 5, 6, 7, 2054, 10, 11, 2064, 16], 7: [1, 2, 6, 2054, 2058, 10, 21, 32, 34, 2085], 8: [1, 2050, 3, 4, 5, 6, 2051, 2053, 9, 2054], 9: [1, 2, 6, 11, 16, 21, 25, 2076, 2078, 2080], 10: [1, 2050, 3, 4, 5, 6, 7, 2052, 2053, 10], 11: [3, 2054, 6, 16, 22, 42, 45, 50, 2102, 2108], 12: [3072, 2565, 3081, 3462, 918, 14, 527, 3599, 3089, 2066], 13: [1, 2, 6, 2054, 2058, 10, 21, 32, 34, 2085], 14: [1, 5, 6, 10, 11, 2058, 2064, 17, 2066, 2067], 15: [1, 2, 6, 2054, 2058, 10, 21, 32, 34, 2085], 16: [1, 2, 6, 2054, 2058, 10, 21, 32, 34, 2085], 17: [1, 3, 11, 24, 2072, 2078, 34, 39, 2088, 2100], 18: [1, 2, 3, 4, 2054, 6, 10, 11, 2058, 2060], 19: [1, 2050, 4, 2053, 6, 2054, 10, 11, 2058, 2060], 20: [1, 2, 6, 2054, 2058, 10, 21, 32, 34, 2085], 21: [1, 2, 6, 2054, 20

평가 지표 저장

In [31]:
evaluate_precision_recall(all_user_top_n_recommendations, user_movie_list, 10)

(0.16010928961749055, 0.010795399049630724)

In [32]:
evaluate_recommendation_metrics(user_movie_list, all_user_top_n_recommendations, 10)

(0.026743962842890726, 0.0003311806590495115)